## Importing Packages {-}

In [1]:
import math
import os
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import spacy
import re
import contractions
import nltk
from nltk.tokenize import word_tokenize
from nltk import WordNetLemmatizer
import spacy
nlp = spacy.load('en_core_web_sm')
all_stopwords = nlp.Defaults.stop_words
lemmatizer = WordNetLemmatizer()
sp = spacy.load('en_core_web_sm')
all_stopwords = sp.Defaults.stop_words

from typing import List
import sys

sys.path.append('.')
import pandas as pd
import os

import string
from nltk.corpus import stopwords
from functools import reduce

In [2]:
import warnings
warnings.filterwarnings('ignore', category=DeprecationWarning)

import gensim
import gensim.corpora as corpora
import gensim.models

import os
from gensim.models.wrappers import LdaMallet
os.environ.update({'MALLET_HOME':r'/mallet-2.0.8'})
from gensim.models import CoherenceModel

!pip install pyLDAvis
import pyLDAvis
import pyLDAvis.gensim_models
pyLDAvis.enable_notebook()

import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)

from pprint import pprint

distutils: /Applications/anaconda3/include/python3.8/UNKNOWN
sysconfig: /Applications/anaconda3/include/python3.8
user = False
home = None
root = None
prefix = None
distutils: /Applications/anaconda3/include/python3.8/UNKNOWN
sysconfig: /Applications/anaconda3/include/python3.8
user = False
home = None
root = None
prefix = None


## Importing DataFrame {-}

In [3]:
dia_df = pd.read_csv('/Users/JoKerry/Desktop/CSML1030 - Machine Learning Capstone/mimic_clinical_outcome_prediction/ICD_Prediction/1. data_preparation/dia_df_prepared.csv')
dia_df

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


id                                               text  \
0      159643  CHIEF COMPLAINT: \n\nPRESENT ILLNESS: This 60 ...   
1      147171  CHIEF COMPLAINT: Substernal Chest Pain\n\nPRES...   
2      190531  CHIEF COMPLAINT: chest pain\n\nPRESENT ILLNESS...   
3      140536  CHIEF COMPLAINT: Presented with respiratory di...   
4      172808  CHIEF COMPLAINT: \n\nPRESENT ILLNESS: The pati...   
...       ...                                                ...   
11532  100746  CHIEF COMPLAINT: Hematemesis and fevers\n\nPRE...   
11533  137725  CHIEF COMPLAINT: Altered mental status, fever,...   
11534  159602  CHIEF COMPLAINT: Respiratory distress\n\nPRESE...   
11535  172011  CHIEF COMPLAINT: Chest pain and shortness of b...   
11536  171528  CHIEF COMPLAINT: Chest pain\n\nPRESENT ILLNESS...   

                                             short_codes  top_icd  
0                       424,428,276,997,427,414,412,V458      424  
1                                410,428,997,427,414,458      410  
2      414,428,584,486,411,585,276,250,403,440,V450,2...      414  
3      410,486,276,425,414,427,695,401,416,496,356,43...      410  
4                           410,998,997,427,414,362,V158      410  
...                                                  ...      ...  
11532  038,507,599,999,578,438,995,451,E879,707,496,4...       38  
11533  038,599,584,591,276,293,518,250,294,287,280,40...       38  
11534  038,518,486,584,427,008,496,424,995,519,V440,1...       38  
11535  414,349,518,285,438,997,427,250,412,461,V498,2...      414  
11536  414,281,411,401,272,427,V586,V103,365,715,564,...      414  

[11537 rows x 4 columns]

## Text Cleaning {-}

In [4]:
my_stop_words = ['discharge', 'diagnosis', 'medications', 'medication', 'disposition', 'condition', 'instructions', 
                 'status', 'secondary', 'changes', 'instruction', 'change', 'home', 'name', 'hospital', 'daily',
                'hour', 'follow', 'care', 'time', 'day', 'week', 'with', 'disp', 'discharged', 'admitted', 
                 'namepattern', 'none', 'chief', 'complaint', 'physical', 'exam', 'present', 'illness', 'family',
                 'year', 'history','admission', 'social', 'medical', 'allergies']

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [5]:
X = dia_df.text
X

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0        CHIEF COMPLAINT: \n\nPRESENT ILLNESS: This 60 ...
1        CHIEF COMPLAINT: Substernal Chest Pain\n\nPRES...
2        CHIEF COMPLAINT: chest pain\n\nPRESENT ILLNESS...
3        CHIEF COMPLAINT: Presented with respiratory di...
4        CHIEF COMPLAINT: \n\nPRESENT ILLNESS: The pati...
                               ...                        
11532    CHIEF COMPLAINT: Hematemesis and fevers\n\nPRE...
11533    CHIEF COMPLAINT: Altered mental status, fever,...
11534    CHIEF COMPLAINT: Respiratory distress\n\nPRESE...
11535    CHIEF COMPLAINT: Chest pain and shortness of b...
11536    CHIEF COMPLAINT: Chest pain\n\nPRESENT ILLNESS...
Name: text, Length: 11537, dtype: object

In [6]:
documents = []

stemmer = WordNetLemmatizer()

for sen in range(0, len(X)):
    # Remove all the special characters
    document = re.sub(r'\W', ' ', str(X[sen]))
    # Remove new line characters
    document = document.replace("\n", ' ')
    # Punctuation
    document = re.sub(r'[^\w\s]', ' ', document)
    # remove all single characters
    document = re.sub(r'\s+[a-zA-Z]\s+', ' ', document)
    # Remove single characters from the start
    document = re.sub(r'\^[a-zA-Z]\s+', ' ', document) 
    # Substituting multiple spaces with single space
    document = re.sub(r'\s+', ' ', document, flags=re.I)
    # Removing prefixed 'b'
    document = re.sub(r'^b\s+', '', document)
    #Removing Numbers
    document = ''.join(i for i in document if not i.isdigit())
    #Removing Stopwords
    document = ' '.join([i for i in document.split() if not i in all_stopwords])
    #Removing certain sized words
    document = ' '.join([i for i in document.split() if len(i)>3])
    # Contractions
    document = contractions.fix(document)
    # Converting to Lowercase
    document = document.lower()
    # Lemmatization
    document = document.split()
    document = [stemmer.lemmatize(word) for word in document]
    document = ' '.join(document)
    #Removing my_stop_words
    document = ' '.join([i for i in document.split() if not i in my_stop_words])
    
    #return document
    documents.append(document)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [7]:
X = documents
X

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


['this white male known murmur childhood post inferior myocardial infarction anteroseptal myocardial infarction post angioplasty since increased dyspnea exertion echocardiogram revealed aortic stenosis gradient ejection fraction apical akinesis cardiac catheterization revealed ejection fraction mitral regurgitation moderate left anterior descending lesion diagonal lesion right coronary artery occlusion aortic valve replacement coronary artery bypass graft significant skin cancer left shoulder hypothyroidism hypercholesterolemia hypertension coronary artery disease post angioplasty post inferior myocardial infarction anteroseptal myocardial infarction prozac synthroid pravachol toprol altace aspirin allergy known drug allergy significant coronary artery disease smoke cigar occasionally drink alcohol occasionally',
 'substernal chest pain male smoker presented experiencing sscp working excavating shoveling dirt state pain sharp crescendoed initially located right chest progressed involve

In [8]:
tokenized_words = [word_tokenize(i) for i in X]

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [9]:
tokenized_words

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[['this',
  'white',
  'male',
  'known',
  'murmur',
  'childhood',
  'post',
  'inferior',
  'myocardial',
  'infarction',
  'anteroseptal',
  'myocardial',
  'infarction',
  'post',
  'angioplasty',
  'since',
  'increased',
  'dyspnea',
  'exertion',
  'echocardiogram',
  'revealed',
  'aortic',
  'stenosis',
  'gradient',
  'ejection',
  'fraction',
  'apical',
  'akinesis',
  'cardiac',
  'catheterization',
  'revealed',
  'ejection',
  'fraction',
  'mitral',
  'regurgitation',
  'moderate',
  'left',
  'anterior',
  'descending',
  'lesion',
  'diagonal',
  'lesion',
  'right',
  'coronary',
  'artery',
  'occlusion',
  'aortic',
  'valve',
  'replacement',
  'coronary',
  'artery',
  'bypass',
  'graft',
  'significant',
  'skin',
  'cancer',
  'left',
  'shoulder',
  'hypothyroidism',
  'hypercholesterolemia',
  'hypertension',
  'coronary',
  'artery',
  'disease',
  'post',
  'angioplasty',
  'post',
  'inferior',
  'myocardial',
  'infarction',
  'anteroseptal',
  'myocard

In [10]:
topic_modeling_series = pd.Series(tokenized_words)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [11]:
topic_modeling_series

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0        [this, white, male, known, murmur, childhood, ...
1        [substernal, chest, pain, male, smoker, presen...
2        [chest, pain, female, dmii, presented, transfe...
3        [presented, respiratory, distress, outside, tr...
4        [patient, male, previous, coronary, artery, di...
                               ...                        
11532    [hematemesis, fever, copd, residual, left, sid...
11533    [altered, mental, fever, hypotension, patient,...
11534    [respiratory, distress, female, tracheobronchi...
11535    [chest, pain, shortness, breath, this, male, k...
11536    [chest, pain, woman, hypertension, hyperlipide...
Length: 11537, dtype: object

## Topic Modelling {-}

In [12]:
# Create Dictionary
id2word = corpora.Dictionary(topic_modeling_series) #use entire corpus
id2word.filter_extremes(no_below=20, no_above=0.1)

# Create Corpus
texts = topic_modeling_series

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# View
print(corpus)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [13]:
print(id2word)

Dictionary(4484 unique tokens: ['akinesis', 'altace', 'angioplasty', 'anteroseptal', 'apical']...)


/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [14]:
def compute_coherence_values(dictionary, corpus, texts, limit, start=2, step=3):
    """
    Compute c_v coherence for various number of topics

    Parameters:
    ----------
    dictionary : Gensim dictionary
    corpus : Gensim corpus
    texts : List of input texts
    limit : Max num of topics

    Returns:
    -------
    model_list : List of LDA topic models
    coherence_values : Coherence values corresponding to the LDA model with respective number of topics
    """
    coherence_values = []
    model_list = []
    for num_topics in range(start, limit, step):
        print('Calculating {}-topic model'.format(num_topics))
        model = gensim.models.ldamodel.LdaModel(corpus=corpus, num_topics=num_topics, id2word=id2word)
        model_list.append(model)
        coherencemodel = CoherenceModel(model=model, texts=texts, dictionary=dictionary, coherence='c_v')
        coherence_values.append(coherencemodel.get_coherence())

    return model_list, coherence_values


/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [ ]:
limit=40; start=2; step=1;
model_list, coherence_values = compute_coherence_values(dictionary=id2word,
                                                        corpus=corpus,
                                                        texts=texts,
                                                        start=start,
                                                        limit=limit,
                                                        step=step)

In [ ]:
# show graph
x = range(start, limit, step)
plt.figure(figsize=(15, 10))
plt.plot(x, coherence_values)
plt.xlabel("Num Topics")
plt.ylabel("Coherence score")
plt.show()

In [ ]:
# Print the coherence scores
for m, cv in zip(x, coherence_values):
    print("Num Topics =", m, " has Coherence Value of", round(cv, 6))

## 30 Topics {-}

In [16]:
# Building LDA Model = LDA Model removing my_stop_words & featuring 30 topics
lda_model_optimal = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=30, 
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha='auto',
                                           per_word_topics=True)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [17]:
pprint(lda_model_optimal.print_topics(num_topics=30, num_words=15))
doc_lda = lda_model_optimal[corpus]

[(0,
  '0.088*"sodium" + 0.054*"acetaminophen" + 0.053*"docusate" + 0.050*"scale" + '
  '0.047*"sliding" + 0.040*"humalog" + 0.038*"solution" + 0.035*"injection" + '
  '0.031*"lantus" + 0.028*"refill" + 0.028*"ipratropium" + 0.025*"meal" + '
  '0.024*"suspension" + 0.024*"powder" + 0.023*"breakfast"'),
 (1,
  '0.051*"fatigue" + 0.039*"followed" + 0.038*"occupation" + 0.038*"reaction" '
  '+ 0.034*"cataract" + 0.033*"adverse" + 0.033*"cigarette" + 0.030*"hctz" + '
  '0.030*"dental" + 0.029*"premature" + 0.023*"appendectomy" + 0.023*"calcium" '
  '+ 0.022*"multivitamin" + 0.022*"caucasian" + 0.021*"trace"'),
 (2,
  '0.201*"percent" + 0.154*"effusion" + 0.074*"pleural" + 0.071*"filling" + '
  '0.060*"mask" + 0.056*"akinesis" + 0.047*"successful" + 0.044*"depressed" + '
  '0.034*"reduced" + 0.026*"sexual" + 0.025*"portion" + 0.025*"ramus" + '
  '0.023*"irregularity" + 0.022*"vague" + 0.019*"maalox"'),
 (3,
  '0.034*"pink" + 0.034*"conjunctiva" + 0.029*"appropriate" + 0.027*"affect" + '
  '

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [18]:
# Compute Perplexity
print('\nPerplexity: ', lda_model_optimal.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model_optimal, texts=texts, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)



Perplexity:  -12.04150629735776

Coherence Score:  0.4675706063214312


In [19]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim_models.prepare(lda_model_optimal, corpus, id2word)
vis

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
/Applications/anaconda3/lib/python3.8/site-packages/pyLDAvis/_prepare.py:246: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
18     0.213476 -0.001662       1        1  11.912221
8      0.149256 -0.107157       2        1  10.524591
22     0.190262 -0.101525       3        1   9.023097
7      0.176613 -0.061844       4        1   8.341670
11     0.155745  0.056069       5        1   6.110957
27     0.140682 -0.182157       6        1   5.863629
3      0.058355 -0.075139       7        1   4.100473
23     0.017881 -0.004982       8        1   3.795810
19    -0.007659  0.015843       9        1   3.602330
1      0.014989 -0.132039      10        1   3.426068
20     0.121238  0.152453      11        1   3.293275
17     0.073217  0.128812      12        1   3.256485
26    -0.027423 -0.005711      13        1   2.750771
13     0.049672  0.182122      14        1   2.732727
5     -0.055815 -0.066116      15        1   2.683578
15    -0.061560  0.022234      16        1   1.856826
6     -0.180929 -0.166758      17        1   1.616636
24    -0.030838  0.141063      18        1   1.477496
12    -0.189637 -0.170931      19        1   1.454302
9     -0.071071  0.038571      20        1   1.453158
4     -0.010663  0.158831      21        1   1.423914
29    -0.068336  0.039833      22        1   1.361009
0     -0.069383 -0.080969      23        1   1.315704
28    -0.091132  0.055924      24        1   1.294425
16    -0.084910  0.044437      25        1   1.199527
10    -0.078525  0.065810      26        1   1.146470
21    -0.040678 -0.113179      27        1   1.065721
25    -0.090524  0.038624      28        1   0.842382
2     -0.103708  0.073987      29        1   0.622206
14    -0.098593  0.055557      30        1   0.452541, topic_info=                Term         Freq        Total Category  logprob  loglift
1164           mouth  5304.000000  5304.000000  Default  30.0000  30.0000
12            mitral  2549.000000  2549.000000  Default  29.0000  29.0000
10             graft  2250.000000  2250.000000  Default  28.0000  28.0000
183            other  2595.000000  2595.000000  Default  27.0000  27.0000
233          capsule  2433.000000  2433.000000  Default  26.0000  26.0000
...              ...          ...          ...      ...      ...      ...
8           diagonal     0.046104   710.562017  Topic30 -11.3468  -4.2449
9           gradient     0.046104   489.702026  Topic30 -11.3468  -3.8726
10             graft     0.046104  2250.002605  Topic30 -11.3468  -5.3975
11    hypothyroidism     0.046104  1344.807644  Topic30 -11.3468  -4.8828
12            mitral     0.046104  2549.390508  Topic30 -11.3468  -5.5224

[1241 rows x 6 columns], token_table=      Topic      Freq         Term
term                              
2346     10  0.991061         abdm
223       7  0.995449   abdominial
2134     20  0.994709     ablation
803      15  0.998898     abnormal
1412      8  0.996097  abnormality
...     ...       ...          ...
1241      9  0.997947      zestril
1313     15  0.995588        zetia
1050      9  0.978629        zocor
1050     10  0.018846        zocor
754       2  0.999296        zosyn

[1521 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[19, 9, 23, 8, 12, 28, 4, 24, 20, 2, 21, 18, 27, 14, 6, 16, 7, 25, 13, 10, 5, 30, 1, 29, 17, 11, 22, 26, 3, 15])

## Vectors For Probabilities - 30 Topics {-}

In [20]:
vector = lda_model_optimal[corpus]  # get topic probability distribution for a document
vector

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [21]:
def Extract(vector):
    return [item[0] for item in vector]

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [22]:
vector_prob = Extract(vector)
vector_prob

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[[(1, 0.046487845),
  (2, 0.02365306),
  (4, 0.08802716),
  (5, 0.035813715),
  (7, 0.030872144),
  (8, 0.032395937),
  (9, 0.057401787),
  (11, 0.052130997),
  (13, 0.11828491),
  (14, 0.022907482),
  (16, 0.047231898),
  (17, 0.031580612),
  (18, 0.05853103),
  (19, 0.019997105),
  (20, 0.023581184),
  (22, 0.123324186),
  (23, 0.015507214),
  (24, 0.031072333),
  (26, 0.054320537),
  (27, 0.023291131)],
 [(1, 0.031639263),
  (3, 0.090563536),
  (7, 0.12297248),
  (8, 0.015528507),
  (10, 0.03691357),
  (11, 0.14802018),
  (15, 0.012630729),
  (17, 0.090573415),
  (18, 0.22942747),
  (20, 0.019825412),
  (22, 0.08532392),
  (24, 0.010949184),
  (27, 0.03418546),
  (28, 0.011465518)],
 [(0, 0.114270926),
  (1, 0.014984777),
  (3, 0.19848226),
  (5, 0.013868697),
  (7, 0.012054137),
  (8, 0.040190678),
  (9, 0.016495164),
  (11, 0.056061782),
  (13, 0.024288863),
  (16, 0.018091599),
  (18, 0.2328508),
  (19, 0.035693426),
  (22, 0.13284445),
  (27, 0.012762237)],
 [(1, 0.02537965),
  

## Aligning Index with Column Titles - 30 Topics {-}

In [59]:
optimal_topics = 30

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [60]:
def clean_vector(vector_prob, optimal_topics):
    full_set = (range(0, optimal_topics))
    cleaned_vectors = []
    for vector in vector_prob:
        topics = [x[0] for x in vector]
        diff = set(full_set).difference(set(topics))
        diff_sort = sorted(list(diff))
        diff_sort_0 = [(x, 0) for x in diff_sort]
        combined = diff_sort_0 + vector
        sorted_combined = sorted(combined, key=lambda x: x[0])
        cleaned_vectors.append(sorted_combined)
    return cleaned_vectors

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [62]:
cleaned_vectors = clean_vector(vector_prob, optimal_topics)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [63]:
cleaned_vectors[0]

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[(0, 0),
 (1, 0.046487845),
 (2, 0.02365306),
 (3, 0),
 (4, 0.08802716),
 (5, 0.035813715),
 (6, 0),
 (7, 0.030872144),
 (8, 0.032395937),
 (9, 0.057401787),
 (10, 0),
 (11, 0.052130997),
 (12, 0),
 (13, 0.11828491),
 (14, 0.022907482),
 (15, 0),
 (16, 0.047231898),
 (17, 0.031580612),
 (18, 0.05853103),
 (19, 0.019997105),
 (20, 0.023581184),
 (21, 0),
 (22, 0.123324186),
 (23, 0.015507214),
 (24, 0.031072333),
 (25, 0),
 (26, 0.054320537),
 (27, 0.023291131),
 (28, 0),
 (29, 0)]

In [64]:
vector_prob_df = pd.DataFrame(cleaned_vectors, columns=list(range(0, optimal_topics)))
vector_prob_df

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0                 1                 2                 3   \
0                (0, 0)  (1, 0.046487845)   (2, 0.02365306)            (3, 0)   
1                (0, 0)  (1, 0.031639263)            (2, 0)  (3, 0.090563536)   
2      (0, 0.114270926)  (1, 0.014984777)            (2, 0)   (3, 0.19848226)   
3                (0, 0)   (1, 0.02537965)            (2, 0)  (3, 0.066545494)   
4                (0, 0)   (1, 0.04000686)            (2, 0)            (3, 0)   
...                 ...               ...               ...               ...   
11532   (0, 0.04331472)  (1, 0.014006813)            (2, 0)            (3, 0)   
11533            (0, 0)   (1, 0.03777725)            (2, 0)  (3, 0.015729781)   
11534            (0, 0)  (1, 0.011576893)  (2, 0.014343587)            (3, 0)   
11535            (0, 0)  (1, 0.094550855)            (2, 0)            (3, 0)   
11536  (0, 0.013023495)   (1, 0.11844286)            (2, 0)            (3, 0)   

                     4                 5                 6                 7   \
0       (4, 0.08802716)  (5, 0.035813715)            (6, 0)  (7, 0.030872144)   
1                (4, 0)            (5, 0)            (6, 0)   (7, 0.12297248)   
2                (4, 0)  (5, 0.013868697)            (6, 0)  (7, 0.012054137)   
3                (4, 0)            (5, 0)   (6, 0.13458543)   (7, 0.10361239)   
4                (4, 0)   (5, 0.02476675)            (6, 0)   (7, 0.03433677)   
...                 ...               ...               ...               ...   
11532            (4, 0)  (5, 0.016131021)  (6, 0.020034084)     (7, 0.194499)   
11533  (4, 0.012096911)  (5, 0.015317122)            (6, 0)   (7, 0.09409068)   
11534  (4, 0.028799197)            (5, 0)            (6, 0)   (7, 0.29734334)   
11535            (4, 0)   (5, 0.05163771)            (6, 0)  (7, 0.027551256)   
11536            (4, 0)  (5, 0.019117115)   (6, 0.06324712)  (7, 0.019041598)   

                     8                 9   ...                 20  \
0      (8, 0.032395937)  (9, 0.057401787)  ...  (20, 0.023581184)   
1      (8, 0.015528507)            (9, 0)  ...  (20, 0.019825412)   
2      (8, 0.040190678)  (9, 0.016495164)  ...            (20, 0)   
3       (8, 0.09096097)   (9, 0.03427427)  ...  (20, 0.026822709)   
4      (8, 0.022586387)            (9, 0)  ...   (20, 0.10900499)   
...                 ...               ...  ...                ...   
11532   (8, 0.19660434)            (9, 0)  ...            (20, 0)   
11533     (8, 0.208321)  (9, 0.020484047)  ...            (20, 0)   
11534    (8, 0.2024129)   (9, 0.02945317)  ...            (20, 0)   
11535   (8, 0.03118613)            (9, 0)  ...  (20, 0.057813816)   
11536   (8, 0.06536154)  (9, 0.015107123)  ...  (20, 0.037087888)   

                      21                 22                 23  \
0                (21, 0)  (22, 0.123324186)  (23, 0.015507214)   
1                (21, 0)   (22, 0.08532392)            (23, 0)   
2                (21, 0)   (22, 0.13284445)            (23, 0)   
3                (21, 0)  (22, 0.049148697)   (23, 0.02365875)   
4       (21, 0.06048999)   (22, 0.14068562)  (23, 0.010724442)   
...                  ...                ...                ...   
11532            (21, 0)  (22, 0.041774288)  (23, 0.044705506)   
11533  (21, 0.023938866)  (22, 0.057606027)   (23, 0.04133107)   
11534            (21, 0)    (22, 0.0570929)  (23, 0.021253271)   
11535   (21, 0.04037349)   (22, 0.25325128)  (23, 0.013379223)   
11536  (21, 0.014236534)   (22, 0.14363445)  (23, 0.019103646)   

                      24                 25                 26  \
0      (24, 0.031072333)            (25, 0)  (26, 0.054320537)   
1      (24, 0.010949184)            (25, 0)            (26, 0)   
2                (24, 0)            (25, 0)            (26, 0)   
3                (24, 0)            (25, 0)  (26, 0.026124299)   
4       (24, 0.03393329)            (25, 0)            (26, 0)   
...                  ...                ...              

In [26]:
# vector_prob_df = pd.DataFrame(vector_prob, columns=[0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29])
# vector_prob_df.head()

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [66]:
def clean_df(df):
    #Create empty dataframe copy
    df2 = pd.DataFrame(np.zeros(df.shape), columns = df.columns)
    nrows = df.shape[0]
    ncolumns = df.shape[1]
    #Populate empty dataframe
    for i in range(nrows):
        #Create key:value pair of each row
        rowdict = dict(zip([x[0] for x in df.iloc[i] if x != None], [x[1] for x in df.iloc[i] if x != None]))
        #Populate row based off of 
        for j in range(ncolumns):
            if j in rowdict.keys():
                df2.iloc[i][j] = rowdict[j]
            else:
                df2.iloc[i][j] = None
    return df2

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [67]:
vector_prob_df_align = clean_df(vector_prob_df)
vector_prob_df_align.head()

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0         1         2         3         4         5         6   \
0  0.000000  0.046488  0.023653  0.000000  0.088027  0.035814  0.000000   
1  0.000000  0.031639  0.000000  0.090564  0.000000  0.000000  0.000000   
2  0.114271  0.014985  0.000000  0.198482  0.000000  0.013869  0.000000   
3  0.000000  0.025380  0.000000  0.066545  0.000000  0.000000  0.134585   
4  0.000000  0.040007  0.000000  0.000000  0.000000  0.024767  0.000000   

         7         8         9   ...        20       21        22        23  \
0  0.030872  0.032396  0.057402  ...  0.023581  0.00000  0.123324  0.015507   
1  0.122972  0.015529  0.000000  ...  0.019825  0.00000  0.085324  0.000000   
2  0.012054  0.040191  0.016495  ...  0.000000  0.00000  0.132844  0.000000   
3  0.103612  0.090961  0.034274  ...  0.026823  0.00000  0.049149  0.023659   
4  0.034337  0.022586  0.000000  ...  0.109005  0.06049  0.140686  0.010724   

         24   25        26        27        28   29  
0  0.031072  0.0  0.054321  0.023291  0.000000  0.0  
1  0.010949  0.0  0.000000  0.034185  0.011466  0.0  
2  0.000000  0.0  0.000000  0.012762  0.000000  0.0  
3  0.000000  0.0  0.026124  0.043902  0.035328  0.0  
4  0.033933  0.0  0.000000  0.017591  0.000000  0.0  

[5 rows x 30 columns]

In [68]:
vector_prob_df_align.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11537 entries, 0 to 11536
Data columns (total 30 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   0       11537 non-null  float64
 1   1       11537 non-null  float64
 2   2       11537 non-null  float64
 3   3       11537 non-null  float64
 4   4       11537 non-null  float64
 5   5       11537 non-null  float64
 6   6       11537 non-null  float64
 7   7       11537 non-null  float64
 8   8       11537 non-null  float64
 9   9       11537 non-null  float64
 10  10      11537 non-null  float64
 11  11      11537 non-null  float64
 12  12      11537 non-null  float64
 13  13      11537 non-null  float64
 14  14      11537 non-null  float64
 15  15      11537 non-null  float64
 16  16      11537 non-null  float64
 17  17      11537 non-null  float64
 18  18      11537 non-null  float64
 19  19      11537 non-null  float64
 20  20      11537 non-null  float64
 21  21      11537 non-null  float64
 22

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [69]:
vector_prob_df_align

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0         1         2         3         4         5         6   \
0      0.000000  0.046488  0.023653  0.000000  0.088027  0.035814  0.000000   
1      0.000000  0.031639  0.000000  0.090564  0.000000  0.000000  0.000000   
2      0.114271  0.014985  0.000000  0.198482  0.000000  0.013869  0.000000   
3      0.000000  0.025380  0.000000  0.066545  0.000000  0.000000  0.134585   
4      0.000000  0.040007  0.000000  0.000000  0.000000  0.024767  0.000000   
...         ...       ...       ...       ...       ...       ...       ...   
11532  0.043315  0.014007  0.000000  0.000000  0.000000  0.016131  0.020034   
11533  0.000000  0.037777  0.000000  0.015730  0.012097  0.015317  0.000000   
11534  0.000000  0.011577  0.014344  0.000000  0.028799  0.000000  0.000000   
11535  0.000000  0.094551  0.000000  0.000000  0.000000  0.051638  0.000000   
11536  0.013023  0.118443  0.000000  0.000000  0.000000  0.019117  0.063247   

             7         8         9   ...        20        21        22  \
0      0.030872  0.032396  0.057402  ...  0.023581  0.000000  0.123324   
1      0.122972  0.015529  0.000000  ...  0.019825  0.000000  0.085324   
2      0.012054  0.040191  0.016495  ...  0.000000  0.000000  0.132844   
3      0.103612  0.090961  0.034274  ...  0.026823  0.000000  0.049149   
4      0.034337  0.022586  0.000000  ...  0.109005  0.060490  0.140686   
...         ...       ...       ...  ...       ...       ...       ...   
11532  0.194499  0.196604  0.000000  ...  0.000000  0.000000  0.041774   
11533  0.094091  0.208321  0.020484  ...  0.000000  0.023939  0.057606   
11534  0.297343  0.202413  0.029453  ...  0.000000  0.000000  0.057093   
11535  0.027551  0.031186  0.000000  ...  0.057814  0.040373  0.253251   
11536  0.019042  0.065362  0.015107  ...  0.037088  0.014237  0.143634   

             23        24        25        26        27        28        29  
0      0.015507  0.031072  0.000000  0.054321  0.023291  0.000000  0.000000  
1      0.000000  0.010949  0.000000  0.000000  0.034185  0.011466  0.000000  
2      0.000000  0.000000  0.000000  0.000000  0.012762  0.000000  0.000000  
3      0.023659  0.000000  0.000000  0.026124  0.043902  0.035328  0.000000  
4      0.010724  0.033933  0.000000  0.000000  0.017591  0.000000  0.000000  
...         ...       ...       ...       ...       ...       ...       ...  
11532  0.044706  0.000000  0.011600  0.024516  0.094933  0.000000  0.012026  
11533  0.041331  0.000000  0.010813  0.016393  0.195223  0.011687  0.000000  
11534  0.021253  0.000000  0.000000  0.031502  0.025871  0.000000  0.028460  
11535  0.013379  0.000000  0.000000  0.011868  0.020042  0.000000  0.000000  
11536  0.019104  0.000000  0.000000  0.000000  0.073887  0.068730  0.000000  

[11537 rows x 30 columns]

In [70]:
topics = vector_prob_df_align
labels = dia_df['top_icd']

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [71]:
topic_modeling_results_30 = pd.concat([labels, topics], axis=1)
topic_modeling_results_30

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


top_icd         0         1         2         3         4         5  \
0          424  0.000000  0.046488  0.023653  0.000000  0.088027  0.035814   
1          410  0.000000  0.031639  0.000000  0.090564  0.000000  0.000000   
2          414  0.114271  0.014985  0.000000  0.198482  0.000000  0.013869   
3          410  0.000000  0.025380  0.000000  0.066545  0.000000  0.000000   
4          410  0.000000  0.040007  0.000000  0.000000  0.000000  0.024767   
...        ...       ...       ...       ...       ...       ...       ...   
11532       38  0.043315  0.014007  0.000000  0.000000  0.000000  0.016131   
11533       38  0.000000  0.037777  0.000000  0.015730  0.012097  0.015317   
11534       38  0.000000  0.011577  0.014344  0.000000  0.028799  0.000000   
11535      414  0.000000  0.094551  0.000000  0.000000  0.000000  0.051638   
11536      414  0.013023  0.118443  0.000000  0.000000  0.000000  0.019117   

              6         7         8  ...        20        21        22  \
0      0.000000  0.030872  0.032396  ...  0.023581  0.000000  0.123324   
1      0.000000  0.122972  0.015529  ...  0.019825  0.000000  0.085324   
2      0.000000  0.012054  0.040191  ...  0.000000  0.000000  0.132844   
3      0.134585  0.103612  0.090961  ...  0.026823  0.000000  0.049149   
4      0.000000  0.034337  0.022586  ...  0.109005  0.060490  0.140686   
...         ...       ...       ...  ...       ...       ...       ...   
11532  0.020034  0.194499  0.196604  ...  0.000000  0.000000  0.041774   
11533  0.000000  0.094091  0.208321  ...  0.000000  0.023939  0.057606   
11534  0.000000  0.297343  0.202413  ...  0.000000  0.000000  0.057093   
11535  0.000000  0.027551  0.031186  ...  0.057814  0.040373  0.253251   
11536  0.063247  0.019042  0.065362  ...  0.037088  0.014237  0.143634   

             23        24        25        26        27        28        29  
0      0.015507  0.031072  0.000000  0.054321  0.023291  0.000000  0.000000  
1      0.000000  0.010949  0.000000  0.000000  0.034185  0.011466  0.000000  
2      0.000000  0.000000  0.000000  0.000000  0.012762  0.000000  0.000000  
3      0.023659  0.000000  0.000000  0.026124  0.043902  0.035328  0.000000  
4      0.010724  0.033933  0.000000  0.000000  0.017591  0.000000  0.000000  
...         ...       ...       ...       ...       ...       ...       ...  
11532  0.044706  0.000000  0.011600  0.024516  0.094933  0.000000  0.012026  
11533  0.041331  0.000000  0.010813  0.016393  0.195223  0.011687  0.000000  
11534  0.021253  0.000000  0.000000  0.031502  0.025871  0.000000  0.028460  
11535  0.013379  0.000000  0.000000  0.011868  0.020042  0.000000  0.000000  
11536  0.019104  0.000000  0.000000  0.000000  0.073887  0.068730  0.000000  

[11537 rows x 31 columns]

In [72]:
topic_modeling_results_30.isna().sum()

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


top_icd    0
0          0
1          0
2          0
3          0
4          0
5          0
6          0
7          0
8          0
9          0
10         0
11         0
12         0
13         0
14         0
15         0
16         0
17         0
18         0
19         0
20         0
21         0
22         0
23         0
24         0
25         0
26         0
27         0
28         0
29         0
dtype: int64

In [73]:
topic_modeling_results_30 = topic_modeling_results_30.fillna(0)
topic_modeling_results_30

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


top_icd         0         1         2         3         4         5  \
0          424  0.000000  0.046488  0.023653  0.000000  0.088027  0.035814   
1          410  0.000000  0.031639  0.000000  0.090564  0.000000  0.000000   
2          414  0.114271  0.014985  0.000000  0.198482  0.000000  0.013869   
3          410  0.000000  0.025380  0.000000  0.066545  0.000000  0.000000   
4          410  0.000000  0.040007  0.000000  0.000000  0.000000  0.024767   
...        ...       ...       ...       ...       ...       ...       ...   
11532       38  0.043315  0.014007  0.000000  0.000000  0.000000  0.016131   
11533       38  0.000000  0.037777  0.000000  0.015730  0.012097  0.015317   
11534       38  0.000000  0.011577  0.014344  0.000000  0.028799  0.000000   
11535      414  0.000000  0.094551  0.000000  0.000000  0.000000  0.051638   
11536      414  0.013023  0.118443  0.000000  0.000000  0.000000  0.019117   

              6         7         8  ...        20        21        22  \
0      0.000000  0.030872  0.032396  ...  0.023581  0.000000  0.123324   
1      0.000000  0.122972  0.015529  ...  0.019825  0.000000  0.085324   
2      0.000000  0.012054  0.040191  ...  0.000000  0.000000  0.132844   
3      0.134585  0.103612  0.090961  ...  0.026823  0.000000  0.049149   
4      0.000000  0.034337  0.022586  ...  0.109005  0.060490  0.140686   
...         ...       ...       ...  ...       ...       ...       ...   
11532  0.020034  0.194499  0.196604  ...  0.000000  0.000000  0.041774   
11533  0.000000  0.094091  0.208321  ...  0.000000  0.023939  0.057606   
11534  0.000000  0.297343  0.202413  ...  0.000000  0.000000  0.057093   
11535  0.000000  0.027551  0.031186  ...  0.057814  0.040373  0.253251   
11536  0.063247  0.019042  0.065362  ...  0.037088  0.014237  0.143634   

             23        24        25        26        27        28        29  
0      0.015507  0.031072  0.000000  0.054321  0.023291  0.000000  0.000000  
1      0.000000  0.010949  0.000000  0.000000  0.034185  0.011466  0.000000  
2      0.000000  0.000000  0.000000  0.000000  0.012762  0.000000  0.000000  
3      0.023659  0.000000  0.000000  0.026124  0.043902  0.035328  0.000000  
4      0.010724  0.033933  0.000000  0.000000  0.017591  0.000000  0.000000  
...         ...       ...       ...       ...       ...       ...       ...  
11532  0.044706  0.000000  0.011600  0.024516  0.094933  0.000000  0.012026  
11533  0.041331  0.000000  0.010813  0.016393  0.195223  0.011687  0.000000  
11534  0.021253  0.000000  0.000000  0.031502  0.025871  0.000000  0.028460  
11535  0.013379  0.000000  0.000000  0.011868  0.020042  0.000000  0.000000  
11536  0.019104  0.000000  0.000000  0.000000  0.073887  0.068730  0.000000  

[11537 rows x 31 columns]

In [74]:
topic_modeling_results_30.isna().sum()

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


top_icd    0
0          0
1          0
2          0
3          0
4          0
5          0
6          0
7          0
8          0
9          0
10         0
11         0
12         0
13         0
14         0
15         0
16         0
17         0
18         0
19         0
20         0
21         0
22         0
23         0
24         0
25         0
26         0
27         0
28         0
29         0
dtype: int64

## CSV {-}

In [75]:
topic_modeling_results_30.to_csv('topic_model_dia_30_topics.csv', index=False)

/Applications/anaconda3/lib/python3.8/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


## Topic Modeling - 50 Topics {-}

In [ ]:
# # Building LDA Model = LDA Model removing my_stop_words & featuring 30 topics
# lda_model_optimal = gensim.models.ldamodel.LdaModel(corpus=corpus,
#                                            id2word=id2word,
#                                            num_topics=50, 
#                                            random_state=100,
#                                            update_every=1,
#                                            chunksize=100,
#                                            passes=10,
#                                            alpha='auto',
#                                            per_word_topics=True)

In [ ]:
# pprint(lda_model_optimal.print_topics(num_topics=50, num_words=15))
# doc_lda = lda_model_optimal[corpus]

In [ ]:
# # Compute Perplexity
# print('\nPerplexity: ', lda_model_optimal.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# # Compute Coherence Score
# coherence_model_lda = CoherenceModel(model=lda_model_optimal, texts=texts, dictionary=id2word, coherence='c_v')
# coherence_lda = coherence_model_lda.get_coherence()
# print('\nCoherence Score: ', coherence_lda)

In [ ]:
# # Visualize the topics
# pyLDAvis.enable_notebook()
# vis = pyLDAvis.gensim_models.prepare(lda_model_optimal, corpus, id2word)
# vis

## Creating Vectors For Probabilities - 50 Topics {-}

In [ ]:
# vector = lda_model_optimal[corpus]  # get topic probability distribution for a document
# vector

In [ ]:
# def Extract(vector):
#     return [item[0] for item in vector]

In [ ]:
# vector_prob = Extract(vector)
# vector_prob

## Align Index With Column Titles - 50 Topics {-}

In [ ]:
# vector_prob_df = pd.DataFrame(vector_prob, columns=[0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,
#                                                     31,32,33,34,35,36,37,38])
# vector_prob_df.head()

In [ ]:
# def clean_df(df):
#     #Create empty dataframe copy
#     df2 = pd.DataFrame(np.zeros(df.shape), columns = df.columns)
#     nrows = df.shape[0]
#     ncolumns = df.shape[1]
#     #Populate empty dataframe
#     for i in range(nrows):
#         #Create key:value pair of each row
#         rowdict = dict(zip([x[0] for x in df.iloc[i] if x != None], [x[1] for x in df.iloc[i] if x != None]))
#         #Populate row based off of 
#         for j in range(ncolumns):
#             if j in rowdict.keys():
#                 df2.iloc[i][j] = rowdict[j]
#             else:
#                 df2.iloc[i][j] = None
#     return df2

In [ ]:
# vector_prob_df_align = clean_df(vector_prob_df)
# vector_prob_df_align.head()

In [ ]:
# vector_prob_df_align.info()

In [ ]:
# vector_prob_df_align

In [ ]:
# topics = vector_prob_df_align
# labels = dia_df['top_icd']

In [ ]:
# topic_modeling_results_50 = pd.concat([labels, topics], axis=1)
# topic_modeling_results_50

In [ ]:
# topic_modeling_results_50.isna().sum()

In [ ]:
# topic_modeling_results_50 = topic_modeling_results_50.fillna(0)
# topic_modeling_results_50

In [ ]:
# topic_modeling_results_50.isna().sum()

## CSV {-}

In [ ]:
# topic_modeling_results_50.to_csv('topic_model_dia_50_topics.csv', index=False)